## Taiwanese Bankruptcy

Commercial loans (generally banks lending to businesses) require significant evaluation prowess given the large amounts at stake and the unique, complex attributes of each borrower. A bank's financial success can vary significantly with its ability to differentiate the risk of the requests and price the loans appropriately (via setting the interest rate) or deny the request.

Researchers exploring commercial loans collected 95 variables on almost 7000 firms in Taiwan and made this data available to the public. The abstract to their research is provided below.

>Effective bankruptcy prediction is critical for financial institutions to make appropriate lending decisions. In general, the input variables (or features), such as financial ratios, and prediction techniques, such as statistical and machine learning techniques, are the two most important factors affecting the prediction performance. While many related works have proposed novel prediction techniques, very few have analyzed the discriminatory power of the features related to bankruptcy prediction. In the literature, in addition to financial ratios (FRs), corporate governance indicators (CGIs) have been found to be another important type of input variable. However, the prediction performance obtained by combining CGIs and FRs has not been fully examined. Only some selected CGIs and FRs have been used in related studies and the chosen features may differ from study to study. Therefore, the aim of this paper is to assess the prediction performance obtained by combining seven different categories of FRs and five different categories of CGIs. The experimental results, based on a real-world dataset from Taiwan, show that the FR categories of solvency and profitability and the CGI categories of board structure and ownership structure are the most important features in bankruptcy prediction. 

>Liang, D., Lu, C.-C., Tsai, C.-F., and Shih, G.-A. (2016) _Financial Ratios and Corporate Governance Indicators in Bankruptcy Prediction: A Comprehensive Study_, European Journal of Operational Research (252:2), pp. 561-572.

We will create a neural net model to use in predicting bankruptcy.

### <font color='firebrick'>1) Notebook Prep</font>

In [55]:
import datetime
from datetime import date, timedelta 
import math
import os
import numpy as np
import pandas as pd
from pandas_datareader._utils import RemoteDataError
import pandas_datareader as web
#-------------------
import tensorflow as tf
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense, Flatten
#-------------------
from sklearn.model_selection import train_test_split
from sklearn import preprocessing  
#-------------------
from scipy import stats
#-------------------


In [56]:
TEST_SIZE = 0.3 # percent or count
EPOCHS = 25
ST_DEV_FOR_OUTLIER = 3
# pd.set_option('display.max_rows', None)

### <font color='firebrick'>2) Retrieve and Review the Data</font>

In [57]:
taiwanese_bankruptcy_data_df = pd.read_csv('taiwanese_bankruptcy_data.csv') 

In [58]:
taiwanese_bankruptcy_data_df.head(12)

Bankrupt?   ROA(C) before interest and depreciation before interest  \
0           1                                           0.370594          
1           1                                           0.464291          
2           1                                           0.426071          
3           1                                           0.399844          
4           1                                           0.465022          
5           1                                           0.388680          
6           0                                           0.390923          
7           0                                           0.508361          
8           0                                           0.488519          
9           0                                           0.495686          
10          0                                           0.482475          
11          0                                           0.444401          

     ROA(A) before interest and % after tax  \
0                                  0.424389   
1                                  0.538214   
2                                  0.499019   
3                                  0.451265   
4                                  0.538432   
5                                  0.415177   
6                                  0.445704   
7                                  0.570922   
8                                  0.545137   
9                                  0.550916   
10                                 0.567543   
11                                 0.549717   

     ROA(B) before interest and depreciation after tax  \
0                                            0.405750    
1                                            0.516730    
2                                            0.472295    
3                                            0.457733    
4                                            0.522298    
5                                            0.419134    
6                                            0.436158    
7                                            0.559077    
8                                            0.543284    
9                                            0.542963    
10                                           0.538198    
11                                           0.498956    

     Operating Gross Margin   Realized Sales Gross Margin  \
0                  0.601457                      0.601457   
1                  0.610235                      0.610235   
2                  0.601450                      0.601364   
3                  0.583541                      0.583541   
4                  0.598783                      0.598783   
5                  0.590171                      0.590251   
6                  0.619950                      0.619950   
7                  0.601738                      0.601717   
8                  0.603612                      0.603612   
9                  0.599209                      0.599209   
10                 0.614026                      0.614026   
11                 0.623712                      0.623712   

     Operating Profit Rate   Pre-tax net Interest Rate  \
0                 0.998969                    0.796887   
1                 0.998946                    0.797380   
2                 0.998857                    0.796403   
3                 0.998700                    0.796967   
4                 0.998973                    0.797366   
5                 0.998758                    0.796903   
6                 0.998993                    0.797012   
7                 0.999009                    0.797449   
8                 0.998961                    0.797414   
9                 0.999001                    0.797404   
10                0.998978                    0.797535   
11                0.998975                    0.797443   

     After-tax net Interest Rate  \
0                       0.808809   
1                       0.809301   
2   

In [59]:
taiwanese_bankruptcy_data_df.shape

(6819, 96)

In [60]:
taiwanese_bankruptcy_data_df['Bankrupt?'].unique()

array([1, 0], dtype=int64)

In [61]:
taiwanese_bankruptcy_data_df.columns

Index(['Bankrupt?', ' ROA(C) before interest and depreciation before interest',
       ' ROA(A) before interest and % after tax',
       ' ROA(B) before interest and depreciation after tax',
       ' Operating Gross Margin', ' Realized Sales Gross Margin',
       ' Operating Profit Rate', ' Pre-tax net Interest Rate',
       ' After-tax net Interest Rate',
       ' Non-industry income and expenditure/revenue',
       ' Continuous interest rate (after tax)', ' Operating Expense Rate',
       ' Research and development expense rate', ' Cash flow rate',
       ' Interest-bearing debt interest rate', ' Tax rate (A)',
       ' Net Value Per Share (B)', ' Net Value Per Share (A)',
       ' Net Value Per Share (C)', ' Persistent EPS in the Last Four Seasons',
       ' Cash Flow Per Share', ' Revenue Per Share (Yuan ¥)',
       ' Operating Profit Per Share (Yuan ¥)',
       ' Per Share Net profit before tax (Yuan ¥)',
       ' Realized Sales Gross Profit Growth Rate',
       ' Operating Profit

In [62]:
taiwanese_bankruptcy_data_df.isnull().sum()

Bankrupt?                                                   0
 ROA(C) before interest and depreciation before interest    0
 ROA(A) before interest and % after tax                     0
 ROA(B) before interest and depreciation after tax          0
 Operating Gross Margin                                     0
 Realized Sales Gross Margin                                0
 Operating Profit Rate                                      0
 Pre-tax net Interest Rate                                  0
 After-tax net Interest Rate                                0
 Non-industry income and expenditure/revenue                0
 Continuous interest rate (after tax)                       0
 Operating Expense Rate                                     0
 Research and development expense rate                      0
 Cash flow rate                                             0
 Interest-bearing debt interest rate                        0
 Tax rate (A)                                               0
 Net Val

In [63]:
# pd.set_option('display.max_rows', None)
taiwanese_bankruptcy_data_df.dtypes

Bankrupt?                                                     int64
 ROA(C) before interest and depreciation before interest    float64
 ROA(A) before interest and % after tax                     float64
 ROA(B) before interest and depreciation after tax          float64
 Operating Gross Margin                                     float64
 Realized Sales Gross Margin                                float64
 Operating Profit Rate                                      float64
 Pre-tax net Interest Rate                                  float64
 After-tax net Interest Rate                                float64
 Non-industry income and expenditure/revenue                float64
 Continuous interest rate (after tax)                       float64
 Operating Expense Rate                                     float64
 Research and development expense rate                      float64
 Cash flow rate                                             float64
 Interest-bearing debt interest rate            

In [85]:
np.abs(stats.zscore(taiwanese_bankruptcy_data_df.loc[ : , taiwanese_bankruptcy_data_df.columns != 'Bankrupt?'])).head(3)

ROA(C) before interest and depreciation before interest  \
0                                           2.217909          
1                                           0.673828          
2                                           1.303672          

    ROA(A) before interest and % after tax  \
0                                 2.045798   
1                                 0.311068   
2                                 0.908420   

    ROA(B) before interest and depreciation after tax  \
0                                           2.400361    
1                                           0.598450    
2                                           1.319910    

    Operating Gross Margin   Realized Sales Gross Margin  \
0                 0.383334                      0.382638   
1                 0.135068                      0.136307   
2                 0.383759                      0.388177   

    Operating Profit Rate   Pre-tax net Interest Rate  \
0                0.016456                    0.023516   
1                0.014671                    0.014799   
2                0.007858                    0.061111   

    After-tax net Interest Rate   Non-industry income and expenditure/revenue  \
0                      0.020165                                      0.087479   
1                      0.015966                                      0.005957   
2                      0.051183                                      0.142238   

    Continuous interest rate (after tax)  ...   Net Income to Total Assets  \
0                               0.031281  ...                     2.254317   
1                               0.009823  ...                     0.309033   
2                               0.086566  ...                     0.820510   

    Total assets to GNP price   No-credit Interval   Gross Profit to Sales  \
0                    0.049491             0.084274                0.383465   
1                    0.049491             0.021388                0.135253   
2                    0.049491             0.005984                0.383698   

    Net Income to Stockholder's Equity   Liability to Equity  \
0                             0.861611              0.680171   
1                             0.029804              0.240685   
2                             0.249820              0.679247   

    Degree of Financial Leverage (DFL)  \
0                             0.060031   
1                            15.129816   
2                             0.062961   

    Interest Coverage Ratio (Interest expense to EBIT)   Net Income Flag  \
0                                           0.098978                 NaN   
1                                           0.364559                 NaN   
2                                           0.125015                 NaN   

    Equity to Liability  
0              0.622067  
1              0.535573  
2              0.621960  

[3 rows x 95 columns]

In [ ]:
np.abs(stats.zscore(taiwanese_bankruptcy_data_df.loc[ : , taiwanese_bankruptcy_data_df.columns != 'Bankrupt?'])) > ST_DEV_FOR_OUTLIER

ROA(C) before interest and depreciation before interest  \
0                                                 False          
1                                                 False          
2                                                 False          
3                                                 False          
4                                                 False          
5                                                 False          
6                                                 False          
7                                                 False          
8                                                 False          
9                                                 False          
10                                                False          
11                                                False          
12                                                False          
13                                                False          
14                                                False          
15                                                False          
16                                                False          
17                                                False          
18                                                False          
19                                                False          
20                                                False          
21                                                False          
22                                                False          
23                                                False          
24                                                False          
25                                                False          
26                                                False          
27                                                False          
28                                                False          
29                                                False          
30                                                False          
31                                                False          
32                                                False          
33                                                False          
34                                                False          
35                                                False          
36                                                False          
37                                                False          
38                                                False          
39                                                False          
40                                                False          
41                                                False          
42                                                False          
43                                                False          
44                                                False          
45                                                False          
46                                                False          
47                                                False          
48                                                False          
49                                                False          
50                                                False          
51                                                False          
52                                                False          
53                                                False          
54                                                False          
55                                                False          
56                                                 True          
57                                                False          
58                                                False          
59                                             

In [ ]:
(np.abs(stats.zscore(taiwanese_bankruptcy_data_df.loc[ : , 
                                                     taiwanese_bankruptcy_data_df.columns != 'Bankrupt?'])) > ST_DEV_FOR_OUTLIER).sum()


 ROA(C) before interest and depreciation before interest     88
 ROA(A) before interest and % after tax                     110
 ROA(B) before interest and depreciation after tax          101
 Operating Gross Margin                                      63
 Realized Sales Gross Margin                                 63
 Operating Profit Rate                                        2
 Pre-tax net Interest Rate                                    7
 After-tax net Interest Rate                                  7
 Non-industry income and expenditure/revenue                  6
 Continuous interest rate (after tax)                         7
 Operating Expense Rate                                       0
 Research and development expense rate                       35
 Cash flow rate                                              89
 Interest-bearing debt interest rate                        146
 Tax rate (A)                                               114
 Net Value Per Share (B)                

### <font color='firebrick'>3) Prepare the Data</font>

In [ ]:
# convert to numpy arrays
X_df = taiwanese_bankruptcy_data_df.drop(['Bankrupt?'],axis=1)
X = X_df.values
y_df = taiwanese_bankruptcy_data_df['Bankrupt?']
y = y_df.values

In [ ]:
type(X)

numpy.ndarray

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X,
                                                    y,
                                                    test_size = TEST_SIZE,
                                                    random_state=42)

# To create a validate data set, we could call `train_test_split` again and pass it X_train and y_train. 

In [ ]:
scaler = preprocessing.MinMaxScaler() 
X_train_scaled = scaler.fit_transform(X_train)

### <font color='firebrick'>4) Define and Compile the Model</font>

In [ ]:
# define model
model = Sequential()

model.add(Flatten(input_shape=([X_train.shape[1]]),
                  name='inputlayer'))

#from tensorflow.keras import layers

model.add(Dense(60, activation='relu', 
                kernel_initializer='he_normal', 
                name='hiddenlayer1'))

model.add(Dense(2, activation='softmax',name='outputlayer'))
# model.add(Dense(1, activation='sigmoid',name='thirdlayer')) # for use with binary_crossentropy

In [ ]:
# compile the model
model.compile(optimizer='adam', 
              loss='sparse_categorical_crossentropy',  
#             loss='binary_crossentropy',  # for use with sigmoid output layer
              metrics=['accuracy', 'SparseCategoricalAccuracy']
              ) 


### <font color='firebrick'>5) Fit and Evaluate the Model</font>

In [ ]:
# fit the model
model.fit(X_train_scaled, 
          y_train, 
          epochs=EPOCHS,
#         validation_data=(x_val, y_val)
          batch_size=32, 
          verbose=1)


Epoch 1/25


150/150 [==============================] - 1s 1ms/step - loss: 0.1476 - accuracy: 0.9650 - sparse_categorical_accuracy: 0.9650
Epoch 2/25
150/150 [==============================] - 0s 1ms/step - loss: 0.1274 - accuracy: 0.9702 - sparse_categorical_accuracy: 0.9702
Epoch 3/25
150/150 [==============================] - 0s 1ms/step - loss: 0.1212 - accuracy: 0.9702 - sparse_categorical_accuracy: 0.9702
Epoch 4/25
150/150 [==============================] - 0s 1ms/step - loss: 0.1140 - accuracy: 0.9698 - sparse_categorical_accuracy: 0.9698
Epoch 5/25
150/150 [==============================] - 0s 1ms/step - loss: 0.1080 - accuracy: 0.9698 - sparse_categorical_accuracy: 0.9698
Epoch 6/25
150/150 [==============================] - 0s 1ms/step - loss: 0.1033 - accuracy: 0.9707 - sparse_categorical_accuracy: 0.9707
Epoch 7/25
150/150 [==============================] - 0s 1ms/step - loss: 0.1025 - accuracy: 0.9702 - sparse_categorical_accuracy: 0.9702
Epoch 8/25
150/150 [=========================

In [ ]:
X_test_scaled = scaler.transform(X_test)

In [ ]:
# evaluate the model
model.evaluate(X_test_scaled, y_test, verbose=0)

[0.11483033746480942, 0.9652981162071228, 0.9652981162071228]

### <font color='firebrick'>6) Deploy, Predict and Act</font>

Next steps would be to set up a solution to allow the model (specifically, the `predict` method) to be called remotely via an API. 

An external system (e.g., a loan application processing system) would now include a call to a server (probably via the REST-consistent protocol like HTTP) with the name of the function requested (e.g., `predict_payoff_success()`), passing the data, and receiving back a probability of payoff for each loan. 

In [ ]:
def predict_payoff_success(dataset):
    '''Mock function that resembles what might be called remotely across systems'''
    dataset_np = dataset.values  # may not be necessary
    dataset_np_scaled = scaler.transform(dataset_np)
    prediction_array = model.predict(dataset_np_scaled) # see also model.predict_classes(X_test_scaled)
    return prediction_array[:,0] # return the probability of success (first column) or bankruptcy (second column)

#### Set Up

Our loan application system will call our model's `predict_payoff_success()` and then, based on the probability of payoff, will suggest:

* Rejecting the loan
* Approving the loan but at a higher interest rate than market (see the `risk_adjusted_rate()` function
* Approving the loan at the market rate

The market rate will be determined by the moving average of the last week of 90 day AA commercial paper rates as provided by the Federal Reserve [90-Day AA Financial Commercial Paper Interest Rate (DCPF3M)](https://fred.stlouisfed.org/series/DCPF3M , "90-Day AA Financial Commercial Paper Interest Rate (DCPF3M)").

In [ ]:
today = datetime.date.today()
last_week = datetime.date.today() - datetime.timedelta(7)
commerical_paper_rate = 0

try:
    commerical_paper_rate = web.DataReader('DCPF3M','fred',last_week, today)["DCPF3M"].mean()
#    commerical_paper_rate = pdr.DataReader("DCPF3M", "fred", last_week, today)["DCPF3M"].mean()
#    commerical_paper_rate = pdr.fred.FredReader("DCPF3M", "fred", last_week, today)["DCPF3M"].mean()
except RemoteDataError:
    commerical_paper_rate = 5.21
    print('FRED access error')

if commerical_paper_rate == 0 | math.isnan(commerical_paper_rate):
    commerical_paper_rate = 5.23

print(commerical_paper_rate)

5.260000000000001


In [ ]:
def risk_adjusted_rate(risk, rate):
    '''Adjusts interests rates to charge based on risk profile'''
    return rate + (1-risk)

In [ ]:
new_data = pd.read_csv('taiwanese_new_data.csv')
y_pred = predict_payoff_success(new_data)
print(y_pred)

1/1 [==============================] - 0s 90ms/step
[0.9950671  0.8737715  0.96637225 0.7724457  0.95326215 0.9976376
 0.97726864 0.99630415 0.99595535 0.96608424 0.99303293 0.99809605
 0.9794953  0.95492953 0.9664842  0.999      0.9931958  0.9989046
 0.95388407 0.9872573 ]


In [ ]:
for _ in y_pred:
    print(f"{_:.0%}")

100%
87%
97%
77%
95%
100%
98%
100%
100%
97%
99%
100%
98%
95%
97%
100%
99%
100%
95%
99%


In [ ]:
for _ in range(y_pred.shape[0]):
    if y_pred[_] < 0.40:
        print(f"Reject this loan application")
    elif y_pred[_] > 0.90:
        print(f"Approve this loan application at  {commerical_paper_rate/100:.2%}")
    else: 
        print(f"Approve this risky loan application at {risk_adjusted_rate(y_pred[_], commerical_paper_rate)/100:.4%}")
    print('―' * 50) 

Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this risky loan application at 5.3862%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this risky loan application at 5.4876%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――――――――――――――――
Approve this loan application at  5.26%
――――――――――――――――――――――――――――――――――――

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=073a5ba6-5e7f-487e-b570-b959ffadafe0' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>